<a href="https://colab.research.google.com/github/joon-ho-jeong/volov10_video/blob/main/yolov10_video.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# 필요한 패키지 설치
!pip install -U ultralytics opencv-python-headless yt-dlp

# FFmpeg 설치
!apt-get update
!apt-get install -y ffmpeg

from ultralytics import YOLO
import cv2
import yt_dlp
import os
import time
from IPython.display import HTML
from base64 import b64encode
import subprocess

def download_youtube_video(youtube_url, output_path='video.mp4'):
    """YouTube 영상 다운로드"""
    try:
        ydl_opts = {
            'format': 'best[height<=720]',
            'outtmpl': output_path,
        }

        with yt_dlp.YoutubeDL(ydl_opts) as ydl:
            print("동영상 다운로드 중...")
            ydl.download([youtube_url])

        return output_path
    except Exception as e:
        print(f"동영상 다운로드 중 에러 발생: {str(e)}")
        return None

def process_video(model, video_path, output_path='output_temp.avi', skip_frames=2):
    """비디오에 대해 객체 탐지 수행"""
    try:
        cap = cv2.VideoCapture(video_path)
        if not cap.isOpened():
            raise Exception("비디오 파일을 열 수 없습니다.")

        width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
        height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
        fps = int(cap.get(cv2.CAP_PROP_FPS))
        total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))

        output_fps = fps // skip_frames
        print(f"비디오 정보: {width}x{height} @ {fps}fps → {output_fps}fps")

        fourcc = cv2.VideoWriter_fourcc(*'XVID')
        out = cv2.VideoWriter(output_path, fourcc, output_fps, (width, height))

        frame_count = 0
        processed_count = 0
        start_time = time.time()

        while cap.isOpened():
            success, frame = cap.read()
            frame_count += 1

            if not success:
                break

            if frame_count % skip_frames != 0:
                continue

            results = model.predict(frame, show=False)
            annotated_frame = results[0].plot()

            # BGR to RGB 변환
            annotated_frame = cv2.cvtColor(annotated_frame, cv2.COLOR_BGR2RGB)
            out.write(cv2.cvtColor(annotated_frame, cv2.COLOR_RGB2BGR))

            processed_count += 1

            if processed_count % 10 == 0:
                elapsed_time = time.time() - start_time
                progress = (frame_count / total_frames) * 100
                fps_processing = processed_count / elapsed_time
                remaining_frames = (total_frames - frame_count) // skip_frames
                eta = remaining_frames / fps_processing if fps_processing > 0 else 0

                print(f'진행률: {progress:.1f}% | 처리 속도: {fps_processing:.1f}fps | 남은 시간: {eta:.1f}초')

        cap.release()
        out.release()

        # AVI를 MP4로 변환 (FFmpeg 사용)
        final_output = 'output_final.mp4'
        print("\nMP4로 변환 중...")
        subprocess.run([
            'ffmpeg', '-i', output_path,
            '-c:v', 'libx264',
            '-preset', 'medium',
            '-crf', '23',
            '-c:a', 'aac',
            '-strict', 'experimental',
            final_output
        ])

        # 임시 파일 삭제
        os.remove(output_path)

        total_time = time.time() - start_time
        print(f"\n처리 완료! 총 소요시간: {total_time:.1f}초")

        return final_output

    except Exception as e:
        print(f"비디오 처리 중 에러 발생: {str(e)}")
        return None

def display_video_player(video_path):
    """비디오 플레이어 표시"""
    try:
        mp4 = open(video_path, 'rb').read()
        data_url = f"data:video/mp4;base64,{b64encode(mp4).decode()}"
        return HTML(f"""
        <video width="640" height="480" controls>
            <source src="{data_url}" type="video/mp4">
        </video>
        """)
    except Exception as e:
        print(f"비디오 표시 중 에러 발생: {str(e)}")
        return None

def main():
    try:
        youtube_url = 'https://youtu.be/6pTpD6hBdAE'  # 분석할 유튜브 영상 URL을 입력하세요

        print("YOLOv10 모델 로딩 중...")
        model = YOLO('yolov10n.pt')  # YOLOv10 경량 모델을 사용 (모델 이름은 실제 모델에 맞춰 변경 필요)

        video_path = download_youtube_video(youtube_url)

        if video_path and os.path.exists(video_path):
            output_path = process_video(model, video_path)

            if output_path and os.path.exists(output_path):
                print("\n결과 영상을 재생합니다...")
                return display_video_player(output_path)
            else:
                print("비디오 처리 결과를 찾을 수 없습니다.")
        else:
            print("다운로드된 비디오 파일을 찾을 수 없습니다.")

    except Exception as e:
        print(f"실행 중 에러 발생: {str(e)}")

if __name__ == "__main__":
    display(main())


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 172.1/172.1 kB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.8/883.8 kB 8.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 45.4 MB/s eta 0:00:00
Get:1 https://cloud.r-project.org/bin/linux/ubuntu jammy-cran40/ InRelease [3,626 B]
Hit:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu2204/x86_64  InRelease
Get:3 http://security.ubuntu.com/ubuntu jammy-security InRelease [129 kB]
Hit:4 http://archive.ubuntu.com/ubuntu jammy InRelease
Get:5 http://archive.ubuntu.com/ubuntu jammy-updates InRelease [128 kB]
Get:6 https://r2u.stat.illinois.edu/ubuntu jammy InRelease [6,555 B]
Hit:7 https://ppa.launchpadcontent.net/deadsnakes/ppa/ubuntu jammy InRelease
Hit:8 https://ppa.launchpadcontent.net/graphics-drivers/ppa/ubuntu jammy InRelease
Get:9 http://security.ubuntu.com/ubuntu jammy-security/restricted amd64 Packages [3,275 kB]
Hit:10 https://ppa.launchpadcontent.net/ubuntugis/ppa/ubuntu j

100%|██████████| 5.59M/5.59M [00:00<00:00, 275MB/s]


동영상 다운로드 중...
[youtube] Extracting URL: https://youtu.be/6pTpD6hBdAE
[youtube] 6pTpD6hBdAE: Downloading webpage
[youtube] 6pTpD6hBdAE: Downloading ios player API JSON
[youtube] 6pTpD6hBdAE: Downloading mweb player API JSON
[youtube] 6pTpD6hBdAE: Downloading player 6f0e2ed6
[youtube] 6pTpD6hBdAE: Downloading m3u8 information
[info] 6pTpD6hBdAE: Downloading 1 format(s): 18
[download] Destination: video.mp4
[download] 100% of    2.22MiB in 00:00:00 at 3.42MiB/s   
비디오 정보: 640x360 @ 29fps → 14fps

0: 384x640 14 persons, 97.5ms
Speed: 5.0ms preprocess, 97.5ms inference, 92.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 11 persons, 10.9ms
Speed: 3.3ms preprocess, 10.9ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 12.0ms
Speed: 1.8ms preprocess, 12.0ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 13 persons, 14.5ms
Speed: 2.7ms preprocess, 14.5ms inference, 0.7ms postprocess per image at shape (1, 3,